In [1]:
import torch
import os
model_id = "stabilityai/stable-diffusion-3.5-large-turbo"
from src.sd3_pipeline import VSFStableDiffusion3Pipeline
pipe = VSFStableDiffusion3Pipeline.from_pretrained(
    "stabilityai/stable-diffusion-3.5-large-turbo",
    torch_dtype=torch.bfloat16,
) 

Loading pipeline components...:   0%|          | 0/9 [00:00<?, ?it/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

You set `add_prefix_space`. The tokenizer needs to be converted from the slow tokenizers


In [2]:
from PIL import Image
negative_prompt_image = Image.open("wheel.webp")

In [3]:
import open_clip

model, preprocess_train, preprocess_val = open_clip.create_model_and_transforms('hf-hub:laion/CLIP-ViT-g-14-laion2B-s34B-b88K')
tokenizer = open_clip.get_tokenizer('hf-hub:laion/CLIP-ViT-g-14-laion2B-s34B-b88K')

In [4]:
import torch
import clip
from PIL import Image

device = "cuda" if torch.cuda.is_available() else "cpu"
model_l, preprocess = clip.load("ViT-L/14", device=device)

In [5]:
model = model.to(device)
image = preprocess(negative_prompt_image).unsqueeze(0).to(device)
with torch.no_grad():
    image_features_l = model_l.encode_image(image)
    
image = preprocess_val(negative_prompt_image).unsqueeze(0).to(device)
with torch.no_grad():
    image_features_g = model.encode_image(image) 

In [6]:
text_feature = pipe.encode_prompt('a wheel', 'a wheel', "")

In [7]:
text_feature[0].shape

torch.Size([1, 333, 4096])

In [8]:
prompt_embed, pooled_prompt_embed = pipe._get_clip_prompt_embeds(
    prompt="a wheel",
    clip_model_index=0,
)
prompt_embed_2, pooled_prompt_embed_2 = pipe._get_clip_prompt_embeds(
    prompt="a wheel",
    clip_model_index=1,
)
clip_prompt_embeds = torch.cat([prompt_embed, prompt_embed_2], dim=-1)

In [9]:
prompt_embed.shape, image_features_l.shape

(torch.Size([1, 77, 768]), torch.Size([1, 768]))

In [10]:
prompt_embed_2.shape, image_features_g.shape

(torch.Size([1, 77, 1280]), torch.Size([1, 1024]))

In [11]:
feature = torch.cat([image_features_l], dim=1)
feature = torch.cat([feature, torch.zeros(1, 4096 - 768).to(device)], dim=1)
feature.shape 

torch.Size([1, 4096])

In [12]:
torch.nn.functional.cosine_similarity(feature, text_feature[0][:,:77].mean(1).to(device)) 

tensor([-0.0525], device='cuda:0', grad_fn=<SumBackward1>)

In [13]:
clip_prompt_embeds.shape, torch.cat([image_features_l, image_features_g], dim=1).shape 

(torch.Size([1, 77, 2048]), torch.Size([1, 1792]))

In [14]:
torch.nn.functional.cosine_similarity(feature.mean(1), text_feature[0][:,:77].mean(1).to(device)) 

tensor([0.0223], device='cuda:0', grad_fn=<SumBackward1>)